In [2]:
from confluent_kafka import Consumer, KafkaError
from json import loads
from kafka import KafkaConsumer
from influxdb_client import InfluxDBClient, Point, WritePrecision
from influxdb_client.client.write_api import SYNCHRONOUS
from datetime import datetime

In [3]:
# Kafka broker address
bootstrap_servers = 'localhost:9093'
 
# Kafka topic to consume messages from
kafka_topic = 'QM_data'
 
# Consumer group ID
group_id = 'group1'
 
# InfluxDB connection details
influxdb_host = 'localhost'
influxdb_port = 8086
influxdb_username = 'Rahma'
influxdb_password = 'rahma123'
bucket = "BloodPressure"
organization = "OstProject"
influxdb_token = "NwFT1hvPZogYtaZG4OCUjF0_BJ46riO_DFFXPW6VaHkWQBFcNQdh67nfT6pPuYUH2kWhFDtiY1Cl2BSRAA4VyQ=="

# Create Kafka consumer configuration
consumer_config = {
    'bootstrap.servers': bootstrap_servers,
    'group.id': group_id,
    'auto.offset.reset': 'earliest'
}
 
with InfluxDBClient(url="http://localhost:8086", token=influxdb_token, org=organization,bucket=bucket) as client:
        write_api = client.write_api(write_options=SYNCHRONOUS)
        consumer = KafkaConsumer(kafka_topic, bootstrap_servers=['localhost:9093'],auto_offset_reset='earliest', api_version=(0,10),enable_auto_commit=True,value_deserializer=lambda x: loads(x.decode('utf-8')))
        print("Connection established")
        i=0
        for message in consumer:
            print(f"{message.value}")
 
            dict = message.value
            point = Point("MIMIC")
                   
 
            for key, val in dict.items():
                    if key != 'Timestamp':
                        point.field(key, float(val))
            point.time(datetime.utcnow(), WritePrecision.NS)
           
            write_api.write(bucket, organization, point)
            i+=1
            print("Message sent to influxDB", i)
            

Connection established
{'Timestamp': '2020-10-20 05:50:25', 'RR': '14.2', 'SPO': '99', 'MAP': '70.7', 'SBP': '97.7', 'DBP': '55.7', 'HR': '75.6', 'PP': '42', 'CO': '3175.2'}
Message sent to influxDB 1
{'Timestamp': '2020-10-20 05:51:25', 'RR': '14.2', 'SPO': '99', 'MAP': '69.5', 'SBP': '95.7', 'DBP': '54.8', 'HR': '73', 'PP': '40.9', 'CO': '2985.7'}
Message sent to influxDB 2
{'Timestamp': '2020-10-20 05:52:25', 'RR': '14.4', 'SPO': '99', 'MAP': '71.3', 'SBP': '98.6', 'DBP': '56.2', 'HR': '76.7', 'PP': '42.4', 'CO': '3252.08'}
Message sent to influxDB 3
{'Timestamp': '2020-10-20 05:53:25', 'RR': '15.6', 'SPO': '99', 'MAP': '70.6', 'SBP': '97.5', 'DBP': '55.6', 'HR': '76.3', 'PP': '41.9', 'CO': '3196.97'}
Message sent to influxDB 4
{'Timestamp': '2020-10-20 05:54:25', 'RR': '13.7', 'SPO': '99', 'MAP': '72.2', 'SBP': '99.9', 'DBP': '56.9', 'HR': '75.7', 'PP': '43', 'CO': '3255.1'}
Message sent to influxDB 5
{'Timestamp': '2020-10-20 05:55:25', 'RR': '10.4', 'SPO': '99', 'MAP': '71.7', 'S